# Data Wrangling COVID-19 Mini-Challenge

## Imports/Setup

In [1]:
import pandas as pd
import wikidata_plain_sparql as wikidata

from bokeh.palettes import turbo
from bokeh.plotting import figure, output_notebook, show, gridplot
from bokeh.models import ColumnDataSource, HoverTool

# set bokeh output mode to notebook
output_notebook()

from helper import get_jhu_cached, create_grid, get_bokeh_tools

Loading BokehJS ...

## Worldwide COVID-19 Data

In [2]:
# get all dates from earliest available data until yesterday
all_dates = pd.date_range(start='2020-01-22', end='today')[:-1]

# standardize column names for all entries
def rename_columns(column):
    column_map = {
        'Lat': 'Latitude',
        'Long_': 'Longitude',
        'Incidence_Rate': 'Incident_Rate'
    }
    if column in column_map:
        return column_map[column]
    return column.replace('/', '_').replace('-', '_').replace(' ', '_')

# load data from all dates
all_data = []
for date in all_dates:
    data = pd.read_csv(get_jhu_cached(date))
    data.rename(columns=rename_columns, inplace=True)
    data['Date'] = date
    all_data.append(data)

# combine data from all days
raw_data = pd.concat(all_data)

In [3]:
# standardize country names for all entries
country_mapping = {
    'MS Zaandam|Diamond Princess|Cruise Ship': 'Others', # move cruise ships to others
    'Hong Kong.+': 'Hong Kong',
    'Iran.+': 'Iran',
    '.*Congo.*': 'Congo',
    'Mainland China': 'China',
    '.*Bahamas.*': 'The Bahamas',
    '.*Gambia.*': 'The Gambia',
    'Viet Nam': 'Vietnam',
    'Taiwan\*': 'Taiwan',
    'Cote d\'Ivoire': 'Ivory Coast',
    'Cabo Verde': 'Cape Verde',
    'Russian Federation': 'Russia',
    ' Azerbaijan': 'Azerbaijan',
    'Holy See': 'Vatican City',
    'Republic of Ireland': 'Ireland',
    'Republic of Moldova': 'Moldova',
    'Czechia': 'Czech Republic',
    'Republic of Korea|Korea, South': 'South Korea',
    'Timor-Leste': 'East Timor',
    'Macao SAR|Macau': 'Macao',
    'UK': 'United Kingdom',
    'Jersey|Guernsey': 'Channel Islands',
    'Dominican Republicn Republic|Dominica': 'Dominican Republic'
}

raw_data['Country_Region'].replace(to_replace=country_mapping.keys(), value=country_mapping.values(), regex=True, inplace=True)

In [4]:
# group data by country
daily_updates = raw_data.groupby(['Country_Region', 'Date']).agg(
     Confirmed = ('Confirmed','sum'),
     Deaths = ('Deaths','sum'),
 ).reset_index()

# get changes in data
updates_per_country = daily_updates.groupby('Country_Region')
daily_updates['New_Confirmed'] = updates_per_country['Confirmed'].diff().fillna(0)
daily_updates['New_Deaths'] = updates_per_country['Deaths'].diff().fillna(0)

worldwide_pretty = daily_updates.loc[:, ['Date', 'Country_Region', 'New_Confirmed', 'Confirmed', 'New_Deaths', 'Deaths']]

In [5]:
# get all countries incl. colors
all_countries = daily_updates['Country_Region'].sort_values().unique()
colors = turbo(all_countries.size)

In [6]:
# show new cases
tools = get_bokeh_tools(tooltips=[
        ('Country', '@country'),
        ('Date', '@x{%F}'),
        ('New Cases', '@y{0,0}'),
    ])

new_cases_graph = figure(
    title='New COVID-19 cases per country',
    y_axis_label='new cases',
    x_axis_type='datetime',
    sizing_mode='stretch_width',
    tools=tools)

i = 0
for country in all_countries:
    updates_for_country = daily_updates.loc[daily_updates['Country_Region'] == country]
    data = ColumnDataSource(data={
        'x': updates_for_country['Date'],
        'y': updates_for_country['New_Confirmed'],
        'country': updates_for_country['Country_Region']
    })
    new_cases_graph.line('x', 'y', source=data, line_color=colors[i], line_width=2)
    i += 1
show(new_cases_graph)

In [7]:
# show total cases
tools = get_bokeh_tools(tooltips=[
        ('Country', '@country'),
        ('Date', '@x{%F}'),
        ('Total Cases', '@y{0,0}'),
    ])

total_cases_graph = figure(
    title='Total COVID-19 cases per country',
    y_axis_label='total cases',
    x_axis_type='datetime',
    sizing_mode='stretch_width',
    tools=tools)

i = 0
for country in all_countries:
    updates_for_country = daily_updates.loc[daily_updates['Country_Region'] == country]
    data = ColumnDataSource(data={
        'x': updates_for_country['Date'],
        'y': updates_for_country['Confirmed'],
        'country': updates_for_country['Country_Region']
    })
    total_cases_graph.line('x', 'y', source=data, line_color=colors[i], line_width=2)
    i += 1
show(total_cases_graph)

## Swiss COVID-19 Data

In [8]:
# get population data from WikiData
canton_data = wikidata.query('''
SELECT ?shortCode ?population ?canton WHERE {
  ?canton wdt:P31 wd:Q23058.
  ?canton wdt:P300 ?shortCode.
  OPTIONAL {
    ?canton p:P1082 ?population_stmt. 
    ?population_stmt ps:P1082 ?population.
    ?population_stmt pq:P585 ?population_date.
  }
  FILTER NOT EXISTS {
    ?canton p:P1082/pq:P585 ?population_date_.
    FILTER (?population_date_ > ?population_date)
  }
}
ORDER BY ?shortCode
''')
canton_data.set_index('shortCode', inplace=True)

In [9]:
raw_data = pd.read_csv('https://raw.githubusercontent.com/openZH/covid_19/master/COVID19_Fallzahlen_CH_total_v2.csv')

# convert to date
raw_data['date'] = pd.to_datetime(raw_data['date'])

# remove FL
swiss = raw_data[raw_data['abbreviation_canton_and_fl'] != 'FL']

# only use data after 1st of june
swiss = swiss[swiss['date'] >= '2020-05-31']

# only keep useful entries
conf_cases = swiss.loc[-swiss['ncumul_conf'].isna()].copy()

# get all cantons
all_cantons = conf_cases['abbreviation_canton_and_fl'].unique()
all_cantons.sort()

# calculate new cases
conf_cases['new_cases'] = 0

for canton in all_cantons:
    updates_for_canton = conf_cases.loc[conf_cases['abbreviation_canton_and_fl'] == canton]
    previous_index = None
    total_cases = 0
    for index in updates_for_canton.index:
        if previous_index != None:
            new_cases = conf_cases.at[index, 'ncumul_conf'] - conf_cases.at[previous_index, 'ncumul_conf']
            conf_cases.at[index, 'new_cases'] = new_cases
            conf_cases.at[index, 'new_cases_relative'] = new_cases / int(canton_data.at['CH-' + canton, 'population']) * 100000
            total_cases += new_cases
            conf_cases.at[index, 'total_cases'] = total_cases
            conf_cases.at[index, 'total_cases_relative'] = total_cases / int(canton_data.at['CH-' + canton, 'population']) * 100000
            conf_cases.at[index, 'new_deaths'] = conf_cases.at[index, 'ncumul_deceased'] - conf_cases.at[previous_index, 'ncumul_deceased']
        previous_index = index

conf_cases = conf_cases[conf_cases['date'] >= '2020-06-01']

swiss_pretty = conf_cases.loc[:, ['date', 'abbreviation_canton_and_fl', 'new_cases', 'total_cases', 'new_deaths']]

### New COVID-19 cases per 100'0000 residents

In [10]:
# calculate new cases
graphs = []
max_new_cases = conf_cases['new_cases_relative'].max()
for canton in all_cantons:
    update_for_canton = conf_cases.loc[conf_cases['abbreviation_canton_and_fl'] == canton].copy()
    
    update_for_canton['new_cases_relative_avg'] = update_for_canton['new_cases_relative'].rolling(window=7).mean()

    new_cases_graph = figure(title=canton, y_axis_label='new cases', y_range=[0, max_new_cases], x_axis_type='datetime')
    new_cases_graph.line(update_for_canton['date'], update_for_canton['new_cases_relative'], line_width=1)
    new_cases_graph.line(update_for_canton['date'], update_for_canton['new_cases_relative_avg'], line_color='red', line_width=1)
    graphs.append(new_cases_graph)

show(create_grid(graphs, sizing_mode='scale_width'))

### Total COVID-19 cases since 1st of june per 100'000 residents

In [11]:
# calculate total cases
graphs = []
max_total_cases = conf_cases['total_cases_relative'].max()
for canton in all_cantons:
    update_for_canton = conf_cases.loc[conf_cases['abbreviation_canton_and_fl'] == canton]

    total_cases_graph = figure(title=canton, y_axis_label='total cases', y_range=[0, max_total_cases], x_axis_type='datetime')
    total_cases_graph.line(update_for_canton['date'], update_for_canton['total_cases_relative'], line_width=1)
    graphs.append(total_cases_graph)

show(create_grid(graphs, sizing_mode='scale_width'))

## Final Data Frames

In [12]:
worldwide_pretty

Date                  Country_Region  New_Confirmed  Confirmed  \
0     2020-02-24                     Afghanistan            0.0        1.0   
1     2020-02-25                     Afghanistan            0.0        1.0   
2     2020-02-26                     Afghanistan            0.0        1.0   
3     2020-02-27                     Afghanistan            0.0        1.0   
4     2020-02-28                     Afghanistan            0.0        1.0   
...          ...                             ...            ...        ...   
79822 2020-03-12  occupied Palestinian territory            0.0        0.0   
79823 2020-03-14  occupied Palestinian territory            0.0        0.0   
79824 2020-03-15  occupied Palestinian territory            0.0        0.0   
79825 2020-03-16  occupied Palestinian territory            0.0        0.0   
79826 2020-03-17  occupied Palestinian territory            0.0        0.0   

       New_Deaths  Deaths  
0             0.0     0.0  
1             0.0     0.0  
2             0.0     0.0  
3             0.0     0.0  
4             0.0     0.0  
...           ...     ...  
79822         0.0     0.0  
79823         0.0     0.0  
79824         0.0     0.0  
79825         0.0     0.0  
79826         0.0     0.0  

[79827 rows x 6 columns]

In [13]:
swiss_pretty

date abbreviation_canton_and_fl  new_cases  total_cases  \
2346  2020-06-01                         BL          1          1.0   
2347  2020-06-01                         FR          0          0.0   
2348  2020-06-01                         GE          1          1.0   
2349  2020-06-01                         GR          0          0.0   
2350  2020-06-01                         JU          0          0.0   
...          ...                        ...        ...          ...   
10777 2021-05-04                         SZ         17      10928.0   
10778 2021-05-04                         SH         14       4306.0   
10779 2021-05-04                         TG          0      17447.0   
10780 2021-05-04                         BS         25      11177.0   
10781 2021-05-04                         AI          1        994.0   

       new_deaths  
2346          0.0  
2347          0.0  
2348          0.0  
2349          0.0  
2350          0.0  
...           ...  
10777         0.0  
10778         0.0  
10779         0.0  
10780         0.0  
10781         0.0  

[7902 rows x 5 columns]